In [93]:
%reload_ext autoreload
%autoreload 2

import os
import sys
import zipfile
from types import SimpleNamespace
import folium
import geopandas as gpd

print(os.getcwd())

if os.getcwd().endswith("notebooks"):
    os.chdir("..")
if os.getcwd() not in sys.path:
    print(os.getcwd())
    sys.path.append(os.getcwd())

from src.data_processing import data_from_placename, GEODESIC_EPSG, EQUAL_AREA_EPSG

/home/red/food-deserts-project


# Verify that the files are available
See readme for instructions on how to run the data gathering script. 

In [95]:
gdb_path = 'data/external/svi_tracts_gdb/SVI_2022_US/SVI2022_US_tract.gdb'
if os.path.exists(gdb_path):
    print(f"The file exists at: {gdb_path}")
else:
    print(f"The file does not exist at: {gdb_path}")

The file exists at: data/external/svi_tracts_gdb/SVI_2022_US/SVI2022_US_tract.gdb


# Select a Location and a Radius

In [101]:
# simple description of where you'd like to center your search
# Large/Dense areas will be resource intensive
PLACE = "Albany, NY"
RADIUS = 4000  # radius in meters

# Calculate a reasonable buffer beyond the search radius

This process queries a circular region for grocery stores and the graph created by streets and intersections. Although there are in-library arguments to add a buffer to the search radius, they are primarily concerned with the immediate perimeter of the graph. Since we want to calculate the distance to the nearest grocery store, we need to take some extra steps. 



In [102]:
buffer = min(RADIUS * 0.5, 2000)


## Ingest, join and process the data

The vast majority of the data processing occurs in the data_from_placename function, which relies on a separate file. 

In [103]:
data = SimpleNamespace(
    **data_from_placename(PLACE, RADIUS, buffer=buffer, return_dictionary=True)
)


/home/red/food-deserts-project/venv/lib/python3.10/site-packages/pyproj/transformer.py:817: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  return self._transformer._transform_point(
/home/red/food-deserts-project/venv/lib/python3.10/site-packages/pyproj/transformer.py:817: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  return self._transformer._transform_point(


Function 'fetch_groceries, []' executed in 1.4406 seconds
Function 'fetch_graph, []' executed in 9.1560 seconds
Function 'read_svi, []' executed in 0.0633 seconds
Function 'merge_grocery, []' executed in 0.0166 seconds


/home/red/food-deserts-project/src/data_processing.py:483: UserWarning: discarding the gdf_nodes geometry column, though its values differ from the coordinates in the x and y columns
  # Shortest grocery travel_times
/home/red/food-deserts-project/src/data_processing.py:282: DeprecationWarning: Graph.shortest_paths() is deprecated; use Graph.distances() instead
  )


Function 'add_grocery_travel_time_igraph, []' executed in 0.0705 seconds
Function 'add_grocery_travel_time, []' executed in 0.0707 seconds
Function 'add_pagerank, []' executed in 0.0146 seconds
Function 'add_betweenness, []' executed in 0.6507 seconds
Function 'add_average_to_edge, ['nearest_grocery_time']' executed in 0.0104 seconds
Function 'add_average_to_edge, ['pagerank']' executed in 0.0102 seconds
Function 'merge_svi, []' executed in 0.0273 seconds
Function 'clean_edges, []' executed in 0.0270 seconds
Function 'clean_nodes, []' executed in 0.0435 seconds
Function 'reconcile_nodes_edges, []' executed in 0.0083 seconds
Function 'merge_highway_dummies_to_nodes, []' executed in 0.0076 seconds


/home/red/food-deserts-project/src/data_processing.py:563: UserWarning: discarding the gdf_nodes geometry column, though its values differ from the coordinates in the x and y columns
  


Function 'data_from_placename, ['Albany, NY']' executed in 13.1069 seconds


# Trim and organize the processed data

In [ ]:
gdf_aoa = gpd.GeoSeries([data.aoa], crs=data.edges.crs)
gdf_edges_aoa = data.edges.clip(gdf_aoa)
gdf_groceries = data.grocery
gdf_svi = data.svi.clip(gdf_aoa)

# Pick some SVI variables to analyze

Examples: 
`E_ ` - Estimated number of persons meeting the condition.
`EP ` - Estimated percentage meeting the condition. 
`EPL ` - Estimated percentage, percentile meeting the condition. 




In [181]:
KEY_VARIABLE = "EPL_POV150"
mouseover_cols = gdf_svi.filter(like="RPL_THEME").columns
mouseover_cols = mouseover_cols.to_list() + [KEY_VARIABLE, "geometry"]

In [182]:
m = gdf_svi[mouseover_cols].explore( tiles="cartodb  positron", column="EPL_POV150", cmap="bone_r", )
m = gdf_edges_aoa.explore(
    m=m,
    column="nearest_grocery_time",
    cmap="magma",

)
m = gdf_groceries.explore(m=m, color="green")
m = gdf_aoa.boundary.explore(m=m, tiles="cartodb  positron", color="red")
m